In [22]:
import numpy as np
import torch
import torch.nn as nn
import os
import cv2
import mediapipe as mp

In [23]:
import math

In [24]:
#import import_ipynb
import GRUModel
from GRUModel import DeepResidualBidirGRU, ResidualBlock_1, ResidualBlock_2

In [25]:
path = r"C:\\Users\\janic\\Downloads\\bidigru.pt"

os.path.exists(path)

True

In [26]:
os.getcwd()

'C:\\Users\\janic\\Downloads'

In [27]:
model = torch.load(path, map_location=torch.device('cpu') )
model.eval()

DeepResidualBidirGRU(
  (res_block1): ResidualBlock_1(
    (relu1): Sequential(
      (0): Linear(in_features=30, out_features=30, bias=True)
      (1): ReLU()
    )
    (gru1): GRU(30, 128, batch_first=True, bidirectional=True)
    (relu2): Sequential(
      (0): Linear(in_features=256, out_features=30, bias=True)
      (1): ReLU()
    )
    (gru2): GRU(30, 128, batch_first=True, bidirectional=True)
    (relu3): Sequential(
      (0): Linear(in_features=256, out_features=30, bias=True)
      (1): ReLU()
    )
    (BN): BatchNorm1d(45, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  )
  (res_block2): ResidualBlock_2(
    (gru1): GRU(30, 128, batch_first=True, bidirectional=True)
    (relu2): Sequential(
      (0): Linear(in_features=256, out_features=30, bias=True)
      (1): ReLU()
    )
    (gru2): GRU(30, 128, batch_first=True, bidirectional=True)
    (relu3): Sequential(
      (0): Linear(in_features=256, out_features=30, bias=True)
      (1): ReLU()
    )
    (B

In [28]:
# Initialize MediaPipe Pose and Drawing utilities
mp_pose = mp.solutions.pose
#mp_drawing = mp.solutions.drawing_utils
pose = mp_pose.Pose()


In [29]:
def calculateAngle(landmark1, landmark2, landmark3):
    '''
    This function calculates angle between three different landmarks.
    Args:
        landmark1: The first landmark containing the x,y and z coordinates.
        landmark2: The second landmark containing the x,y and z coordinates.
        landmark3: The third landmark containing the x,y and z coordinates.
    Returns:
        angle: The calculated angle between the three landmarks.

    '''

    # Get the required landmarks coordinates.
    x1, y1, _ = landmark1
    x2, y2, _ = landmark2
    x3, y3, _ = landmark3

    # Calculate the angle between the three points
    angle = math.degrees(math.atan2(y3 - y2, x3 - x2) - math.atan2(y1 - y2, x1 - x2))

    # Check if the angle is less than zero.
    if angle < 0:

        # Add 360 to the found angle.
        angle += 360

    # Return the calculated angle.
    return angle

In [30]:
def angle(mp_pose, landmarks):
    left_hip_angle = calculateAngle(landmarks[mp_pose.PoseLandmark.LEFT_KNEE.value],
                                    landmarks[mp_pose.PoseLandmark.LEFT_HIP.value],
                                    landmarks[mp_pose.PoseLandmark.RIGHT_HIP.value])

    # Get the angle between the right hip, left hip and right knee points
    right_hip_angle = calculateAngle(landmarks[mp_pose.PoseLandmark.LEFT_HIP.value],
                                     landmarks[mp_pose.PoseLandmark.RIGHT_HIP.value],
                                     landmarks[mp_pose.PoseLandmark.RIGHT_KNEE.value])

    # Get the angle between the left hip, knee and ankle points.
    left_knee_angle = calculateAngle(landmarks[mp_pose.PoseLandmark.LEFT_HIP.value],
                                     landmarks[mp_pose.PoseLandmark.LEFT_KNEE.value],
                                     landmarks[mp_pose.PoseLandmark.LEFT_ANKLE.value])

    # Get the angle between the right hip, knee and ankle points
    right_knee_angle = calculateAngle(landmarks[mp_pose.PoseLandmark.RIGHT_ANKLE.value],
                                      landmarks[mp_pose.PoseLandmark.RIGHT_KNEE.value],
                                      landmarks[mp_pose.PoseLandmark.RIGHT_HIP.value])

    # Get the angle between the left elbow, shoulder and hip points.
    left_shoulder_angle = calculateAngle(landmarks[mp_pose.PoseLandmark.LEFT_ELBOW.value],
                                         landmarks[mp_pose.PoseLandmark.LEFT_SHOULDER.value],
                                         landmarks[mp_pose.PoseLandmark.LEFT_HIP.value])

    # Get the angle between the right hip, shoulder and elbow points.
    right_shoulder_angle = calculateAngle(landmarks[mp_pose.PoseLandmark.RIGHT_HIP.value],
                                          landmarks[mp_pose.PoseLandmark.RIGHT_SHOULDER.value],
                                          landmarks[mp_pose.PoseLandmark.RIGHT_ELBOW.value])

    # Get the angle between the left shoulder, elbow and wrist points.
    left_wrist_angle = calculateAngle(landmarks[mp_pose.PoseLandmark.LEFT_ELBOW.value],
                                      landmarks[mp_pose.PoseLandmark.LEFT_WRIST.value],
                                      landmarks[mp_pose.PoseLandmark.LEFT_THUMB.value])

    # Get the angle between the right shoulder, elbow and wrist points.
    right_wrist_angle = calculateAngle(landmarks[mp_pose.PoseLandmark.RIGHT_THUMB.value],
                                       landmarks[mp_pose.PoseLandmark.RIGHT_WRIST.value],
                                       landmarks[mp_pose.PoseLandmark.RIGHT_ELBOW.value])

    # Get the angle between the right shoulder, left shoulder and left elbow points
    left_mouth_angle = calculateAngle(landmarks[mp_pose.PoseLandmark.LEFT_EYE_OUTER.value],
                                      landmarks[mp_pose.PoseLandmark.MOUTH_LEFT.value],
                                      landmarks[mp_pose.PoseLandmark.LEFT_SHOULDER.value])

    # Get the angle between the right shoulder, left shoulder and left elbow points
    right_mouth_angle = calculateAngle(landmarks[mp_pose.PoseLandmark.RIGHT_SHOULDER.value],
                                       landmarks[mp_pose.PoseLandmark.MOUTH_RIGHT.value],
                                       landmarks[mp_pose.PoseLandmark.RIGHT_EYE_OUTER.value])

    angle_list = np.array([left_hip_angle,right_hip_angle,
                   left_knee_angle,right_knee_angle,
                   left_shoulder_angle,right_shoulder_angle,
                   left_wrist_angle,right_wrist_angle,
                   left_mouth_angle,right_mouth_angle])

    return angle_list

In [31]:
def want_landmark(landmark):
    keypoint_data = np.zeros(20)
    keypoint_data[0]= landmark[13].x
    keypoint_data[1]= landmark[23].x
    keypoint_data[2]= landmark[25].x
    keypoint_data[3]= landmark[11].x
    keypoint_data[4]= landmark[15].x
    keypoint_data[5]= landmark[14].x
    keypoint_data[6]= landmark[24].x
    keypoint_data[7]= landmark[26].x
    keypoint_data[8]= landmark[12].x
    keypoint_data[9]= landmark[16].x
    keypoint_data[10]= landmark[13].y
    keypoint_data[11]= landmark[23].y
    keypoint_data[12]= landmark[25].y
    keypoint_data[13]= landmark[11].y
    keypoint_data[14]= landmark[15].y
    keypoint_data[15]= landmark[14].y
    keypoint_data[16]= landmark[24].y
    keypoint_data[17]= landmark[26].y
    keypoint_data[18]= landmark[12].y
    keypoint_data[19]= landmark[16].y

    return keypoint_data

In [32]:
def process_frame(frame):
    landmarks=[]
    keypoint_data_final = []
    # Convert frame to RGB
    frame_rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
    height, width, _ = frame_rgb.shape


    # Use MediaPipe Pose to detect poses
    results = pose.process(frame_rgb)

    #keypoint_data = np.zeros(20)  # Placeholder for storing keypoint data


    if results.pose_landmarks:
        print(results.pose_landmarks.landmark)
        for landmark in results.pose_landmarks.landmark:
            landmarks.append((int(landmark.x * width), int(landmark.y * height),
                                  (landmark.z * width)))

        #for idx, landmark in enumerate(results.pose_landmarks.landmark):
            # Store x and y coordinates of each keypoint
            #keypoint_data[2 * idx] = landmark.x
            #keypoint_data[2 * idx + 1] = landmark.y

        keypoint_data = want_landmark(results.pose_landmarks.landmark)


        angle_list = angle(mp_pose,landmarks)
        keypoint_data_final = np.hstack((keypoint_data , angle_list))

        return keypoint_data_final,angle_list
    else:

        return np.zeros(30),np.zeros(10)

In [33]:
def moving_average(data, window_size):
    return np.convolve(data, np.ones(window_size) / window_size, mode='valid')

In [34]:
demo = np.hstack((0,np.array([1,2,3])))

In [35]:
prevdiff = demo[-1:]

In [36]:
prevdiff

array([3])

In [37]:
def actioncounter(actiontype,angles_array,prevdiff):
    followup_count = 3
    if actiontype == 0 or actiontype == 2:
        joint_index = 0
    else:
        joint_index = 4
    joint_angles = angles_array[:, joint_index]
    print(joint_angles)
    #smoothed_angles = moving_average(joint_angles, 2)
    anglesequence=np.array(joint_angles)
    diffs = np.diff(anglesequence)
    diffs = np.hstack((prevdiff,diffs))
    
    decreasing_to_increasing = (diffs[:-1] < 0) & (diffs[1:] >= 1)
    
    valid_changes = np.zeros_like(decreasing_to_increasing, dtype=bool)

    for i in range(len(decreasing_to_increasing) - followup_count):
        if decreasing_to_increasing[i]:
            if np.all(diffs[i+1:i+1+followup_count] > 0):
                valid_changes[i] = True
    count = np.max(valid_changes)
    prevdiff = diffs[-3:]
    
    
    print(anglesequence)
    print(diffs)
    
    
    return count,prevdiff,anglesequence


In [38]:
def actioncounter22(actiontype,angles_array,prevdiff):
    followup_count = 3
    if actiontype == 0 or actiontype == 2:
        joint_index = 0
    else:
        joint_index = 4
    joint_angles = angles_array[:, joint_index]
    #print(joint_angles)
    #smoothed_angles = moving_average(joint_angles, 2)
    anglesequence=np.array(joint_angles)
    print(anglesequence)
    diffs = np.diff(anglesequence)
    diffs = np.hstack((prevdiff,diffs))
    
    zero_crossings = np.where(np.diff(np.sign(diffs)))[0]
    print(zero_crossings)
    
    #return count,prevdiff

In [48]:
cap = cv2.VideoCapture(0)
keypoint_data_buffer = []
angle_data_buffer  = []
frame_count = 0
starting_frame_count = 45
result_type=''
font = cv2.FONT_HERSHEY_SIMPLEX
counter = 0
prevdiff=np.array([0,0,0])
pose_type=''
stage=''


while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        continue

    #keypoint_data = process_frame(frame)
    
    keypoint_data, angle_data = process_frame(frame)
    if np.any(keypoint_data):
        keypoint_data_buffer.append(keypoint_data)
        angle_data_buffer.append(angle_data)
        frame_count +=1

        #if keypoint_data.any():
        #    print(keypoint_data)

        if frame_count % 10 == 0 and len(keypoint_data_buffer) >= 45:
            lstm_input = np.array(keypoint_data_buffer[-45:])  # Get data from the last 45 frames
            lstm_input = torch.tensor(lstm_input, dtype=torch.float32).unsqueeze(0)  # Add batch dimension
            outputs = model(lstm_input)
            _,predicted = torch.max(outputs,1)
            print("LSTM Model Prediction:", torch.argmax(predicted).item())
            result_type = torch.argmax(predicted).item()
            
        if frame_count % 5 == 0 and len(angle_data_buffer) >= 5:
            if len(angle_data_buffer) >10:
                angle_input_list = angle_data_buffer[-11:]
            else:
                angle_input_list = angle_data_buffer
            angle_input = np.array(angle_input_list)
            count,prevdiff,anglesequence = actioncounter(result_type,angle_input,prevdiff)
            #counter += count
        
            for i in anglesequence:
                print(i)
                if i > 130:
                    stage = 'up'
                    break;
                if i<30 and stage == 'up':
                    stage = "down"
                    counter += 1
                    break;
        print(counter)


        if result_type==0:
            pose_type = 'Jumping Jack'

        if result_type==1:
            pose_type = 'Side Bend'

        if result_type==2:
            pose_type = 'Side Leg'



        cv2.putText(frame,
                    str(pose_type),
                    (50, 50),
                    font, 1,
                    (255, 128, 0),
                    2,
                    cv2.LINE_4)
        cv2.putText(frame,
                    str(stage),
                    (300, 50),
                    font, 1,
                    (255, 128, 0),
                    2,
                    cv2.LINE_4)    
        cv2.putText(frame,
                    str(counter),
                    (450, 50),
                    font, 1,
                    (255, 128, 0),
                    2,
                    cv2.LINE_4)
        cv2.putText(frame,
                    str(angle_data[4]),
                    (500, 50),
                    font, 1,
                    (255, 128, 0),
                    2,
                    cv2.LINE_4)   

        cv2.imshow('Webcam Feed', frame)

        if cv2.waitKey(1) & 0xFF == 27:
            break




pose.close()
cap.release()
cv2.destroyAllWindows()

[x: 1.02226782
y: 0.520981252
z: -0.466759056
visibility: 0.994042754
, x: 1.04405522
y: 0.441032946
z: -0.461506605
visibility: 0.988612771
, x: 1.03234029
y: 0.461881787
z: -0.461548895
visibility: 0.988810599
, x: 1.05149055
y: 0.468711019
z: -0.462275892
visibility: 0.987719178
, x: 0.99435693
y: 0.444357306
z: -0.449528545
visibility: 0.991469502
, x: 0.97940743
y: 0.447255552
z: -0.448593318
visibility: 0.991379499
, x: 0.961253464
y: 0.451084197
z: -0.449369043
visibility: 0.992568195
, x: 1.07820034
y: 0.485611767
z: -0.234289885
visibility: 0.989765465
, x: 0.941372514
y: 0.473560542
z: -0.1553341
visibility: 0.994718075
, x: 1.0492878
y: 0.60358566
z: -0.370629191
visibility: 0.996866405
, x: 0.987354934
y: 0.594796598
z: -0.347653955
visibility: 0.997313261
, x: 1.1826818
y: 0.725410402
z: -0.139945239
visibility: 0.994663179
, x: 0.795479894
y: 0.671091676
z: -0.0485114902
visibility: 0.99925
, x: 1.19379771
y: 1.11335766
z: -0.219457835
visibility: 0.466548651
, x: 0.70624

[x: 1.04239655
y: 0.519181252
z: -0.641692519
visibility: 0.992468715
, x: 1.08336806
y: 0.419470906
z: -0.623782039
visibility: 0.986473322
, x: 1.09307766
y: 0.475196183
z: -0.623667657
visibility: 0.985200107
, x: 1.11211789
y: 0.472038478
z: -0.624385953
visibility: 0.985964656
, x: 1.01312554
y: 0.420440614
z: -0.625303864
visibility: 0.990567
, x: 0.993777454
y: 0.41977641
z: -0.624508739
visibility: 0.989453495
, x: 0.975339055
y: 0.419127524
z: -0.625017881
visibility: 0.991368294
, x: 1.13171661
y: 0.473280698
z: -0.305078894
visibility: 0.986694396
, x: 0.942768753
y: 0.410632461
z: -0.287905633
visibility: 0.992677629
, x: 1.06396139
y: 0.606696
z: -0.506702065
visibility: 0.996021807
, x: 0.998773456
y: 0.58311069
z: -0.501294792
visibility: 0.996683657
, x: 1.21688175
y: 0.697373152
z: -0.11705631
visibility: 0.995007396
, x: 0.823164463
y: 0.649045289
z: -0.163545504
visibility: 0.999223351
, x: 1.2417506
y: 1.11877525
z: -0.0298256241
visibility: 0.394663215
, x: 0.75736

[x: 1.04539609
y: 0.513301611
z: -0.664320529
visibility: 0.990957916
, x: 1.08635926
y: 0.40953961
z: -0.643906
visibility: 0.984635234
, x: 1.11112869
y: 0.426212519
z: -0.64385891
visibility: 0.982573509
, x: 1.11326241
y: 0.467475474
z: -0.644548535
visibility: 0.983711779
, x: 1.01532531
y: 0.414738685
z: -0.646116614
visibility: 0.989401877
, x: 0.995007217
y: 0.415967643
z: -0.645357
visibility: 0.988184631
, x: 0.975777924
y: 0.416983426
z: -0.645940423
visibility: 0.990593195
, x: 1.13299894
y: 0.469106138
z: -0.322998047
visibility: 0.984564066
, x: 0.94425267
y: 0.413072228
z: -0.282838523
visibility: 0.992148459
, x: 1.07772577
y: 0.602143109
z: -0.512530148
visibility: 0.994763076
, x: 1.00499904
y: 0.580887139
z: -0.514910936
visibility: 0.995819092
, x: 1.22483361
y: 0.695204318
z: -0.152726009
visibility: 0.994315684
, x: 0.826803
y: 0.647654116
z: -0.161206827
visibility: 0.999157846
, x: 1.24774432
y: 1.09983516
z: -0.018101532
visibility: 0.323728353
, x: 0.736053
y:

[x: 1.04320359
y: 0.517430961
z: -0.804412067
visibility: 0.990090549
, x: 1.07773268
y: 0.416323274
z: -0.789741874
visibility: 0.983351469
, x: 1.10517716
y: 0.455747277
z: -0.789622962
visibility: 0.981088281
, x: 1.11329639
y: 0.468288
z: -0.790336072
visibility: 0.982342243
, x: 1.01492155
y: 0.418438464
z: -0.788324952
visibility: 0.988695383
, x: 0.995614827
y: 0.418729186
z: -0.787568212
visibility: 0.987539291
, x: 0.976255059
y: 0.41908139
z: -0.787991881
visibility: 0.990104556
, x: 1.13363302
y: 0.468634874
z: -0.451335132
visibility: 0.983103335
, x: 0.944879174
y: 0.414465606
z: -0.419229597
visibility: 0.991684854
, x: 1.07386267
y: 0.605892301
z: -0.658570707
visibility: 0.994121611
, x: 1.00405371
y: 0.582991958
z: -0.649173677
visibility: 0.995270669
, x: 1.22749674
y: 0.68569392
z: -0.212216973
visibility: 0.994109869
, x: 0.821938634
y: 0.65291065
z: -0.223526284
visibility: 0.999117613
, x: 1.26515865
y: 1.08571553
z: -0.0976501256
visibility: 0.281301171
, x: 0.74

[x: 1.03780246
y: 0.50756067
z: -0.53302896
visibility: 0.989800394
, x: 1.06718659
y: 0.411583155
z: -0.518771052
visibility: 0.982933223
, x: 1.0989989
y: 0.425581664
z: -0.518578172
visibility: 0.979995131
, x: 1.12133694
y: 0.465173423
z: -0.519251704
visibility: 0.981603324
, x: 1.01085019
y: 0.407927305
z: -0.514962733
visibility: 0.988665283
, x: 0.993339539
y: 0.407402813
z: -0.51412344
visibility: 0.987354815
, x: 0.975529194
y: 0.407880932
z: -0.514707685
visibility: 0.990315795
, x: 1.14196706
y: 0.466731906
z: -0.247676611
visibility: 0.981795
, x: 0.945413768
y: 0.408359826
z: -0.206325024
visibility: 0.991970956
, x: 1.06621337
y: 0.592268825
z: -0.417069823
visibility: 0.993784249
, x: 1.0024128
y: 0.566988587
z: -0.405081332
visibility: 0.995231
, x: 1.23173487
y: 0.684486628
z: -0.0694422573
visibility: 0.994177043
, x: 0.819375396
y: 0.649850786
z: -0.0948186442
visibility: 0.999224365
, x: 1.27101612
y: 1.07424557
z: 0.0294897817
visibility: 0.257597893
, x: 0.729545

...

[x: 0.404680669
y: 0.396899223
z: -1.08832574
visibility: 0.999325395
, x: 0.431893736
y: 0.337712914
z: -1.037269
visibility: 0.998905838
, x: 0.448215067
y: 0.33829692
z: -1.03763878
visibility: 0.998939514
, x: 0.464004844
y: 0.340239137
z: -1.03777719
visibility: 0.998624206
, x: 0.378394514
y: 0.342022091
z: -1.05807662
visibility: 0.99906975
, x: 0.352470577
y: 0.347150028
z: -1.05799556
visibility: 0.999160469
, x: 0.329315901
y: 0.353815824
z: -1.05874562
visibility: 0.999118865
, x: 0.479704529
y: 0.364549309
z: -0.653050244
visibility: 0.998771369
, x: 0.299961984
y: 0.373987019
z: -0.743756413
visibility: 0.999687731
, x: 0.4300116
y: 0.460652202
z: -0.936473489
visibility: 0.999373853
, x: 0.371178329
y: 0.467006117
z: -0.962973118
visibility: 0.999733388
, x: 0.537527
y: 0.672505558
z: -0.3217583
visibility: 0.996646583
, x: 0.193505228
y: 0.601495862
z: -0.516900599
visibility: 0.99814719
, x: 0.578469634
y: 0.978505492
z: -0.276756585
visibility: 0.196291566
, x: 0.00067

LSTM Model Prediction: 1
[14.29535064 12.48717512 12.57935642 12.80507828 12.53617568 12.55199382
 13.92346558 14.74496784 16.12928727 15.35397261 15.4388992 ]
[14.29535064 12.48717512 12.57935642 12.80507828 12.53617568 12.55199382
 13.92346558 14.74496784 16.12928727 15.35397261 15.4388992 ]
[ 0.22572185 -0.2689026   0.01581814 -1.80817552  0.0921813   0.22572185
 -0.2689026   0.01581814  1.37147176  0.82150226  1.38431944 -0.77531467
  0.08492659]
14.295350644761292
12.487175123404656
12.57935642391862
12.80507827598815
12.536175677671027
12.551993819277657
13.923465577225306
14.744967838437784
16.12928727395253
15.353972606890308
15.43889920153865
31
[x: 0.409067
y: 0.399274558
z: -0.819218934
visibility: 0.999165416
, x: 0.436069
y: 0.341086358
z: -0.754033208
visibility: 0.998681545
, x: 0.452008247
y: 0.341491431
z: -0.754460514
visibility: 0.998718262
, x: 0.467267692
y: 0.342999101
z: -0.754696727
visibility: 0.998344779
, x: 0.380422533
y: 0.344627708
z: -0.78365773
visibilit

[x: 0.435484558
y: 0.39946869
z: -0.901351154
visibility: 0.999352932
, x: 0.457631916
y: 0.340158612
z: -0.831134915
visibility: 0.999093652
, x: 0.473448604
y: 0.340825111
z: -0.83144635
visibility: 0.999078155
, x: 0.487401485
y: 0.342585534
z: -0.831606865
visibility: 0.99884969
, x: 0.404871851
y: 0.344806463
z: -0.868569255
visibility: 0.999224901
, x: 0.378466308
y: 0.350831896
z: -0.868402958
visibility: 0.999283373
, x: 0.351831049
y: 0.358566076
z: -0.869065
visibility: 0.999255
, x: 0.493084192
y: 0.364927471
z: -0.388216019
visibility: 0.998998761
, x: 0.310099304
y: 0.378113091
z: -0.569597363
visibility: 0.999751151
, x: 0.456682503
y: 0.461237609
z: -0.735555053
visibility: 0.999435365
, x: 0.395110786
y: 0.470689774
z: -0.785822272
visibility: 0.999760509
, x: 0.551358759
y: 0.675796926
z: -0.059782695
visibility: 0.996961
, x: 0.197000831
y: 0.602106333
z: -0.438461155
visibility: 0.998213232
, x: 0.601156116
y: 0.980429828
z: 0.0694509223
visibility: 0.112680495
, x: 

[x: 0.455516964
y: 0.436436117
z: -0.998107076
visibility: 0.998776138
, x: 0.480608404
y: 0.378147632
z: -0.932217598
visibility: 0.998391151
, x: 0.496889412
y: 0.379164189
z: -0.932596326
visibility: 0.998186529
, x: 0.510968328
y: 0.380953968
z: -0.932796121
visibility: 0.99770236
, x: 0.426344544
y: 0.376152635
z: -0.968377769
visibility: 0.998735607
, x: 0.402263075
y: 0.377319366
z: -0.9682827
visibility: 0.998812497
, x: 0.378938198
y: 0.380217522
z: -0.968949497
visibility: 0.998815298
, x: 0.514338
y: 0.400729924
z: -0.50605
visibility: 0.998091161
, x: 0.331870377
y: 0.395058662
z: -0.66954267
visibility: 0.999608457
, x: 0.471420288
y: 0.506621778
z: -0.829620957
visibility: 0.998912811
, x: 0.41014424
y: 0.50766623
z: -0.878111839
visibility: 0.999605536
, x: 0.562839925
y: 0.695030093
z: -0.179654792
visibility: 0.993287742
, x: 0.198707938
y: 0.614991724
z: -0.48356539
visibility: 0.997212172
, x: 0.61435318
y: 0.995118797
z: -0.0209736377
visibility: 0.0825218931
, x: -

KeyboardInterrupt: 